In [0]:
# importing necessary libraries
from pyspark.sql.functions import (
    col,
    when,
    hour,
    month,
    year,
    dayofweek,
    dayofmonth,
    date_format,
    unix_timestamp,
    from_unixtime,
    count,
    sum,
    round,
    desc,
    lit,
    substring,
)
import numpy as np
import pandas as pd
from datetime import datetime
import plotly.express as px
import plotly.graph_objects as go

Loading Data
--

In [0]:
# accessing azure cloud storage
storage_account_name = "unifieddatadl02azemtd"
container_name = "cbdtp-data"
sub_directory = "TLC_Data"  # f'{agency_name}/{dataset_name}/{file_name}'

In [0]:
# reading lookup table
sub_directory = "TLC_Data"
file_name = "Taxi_Zone_Lookup.csv"
adlspath = f"abfss://{container_name}@{storage_account_name}.dfs.core.windows.net/{sub_directory}/{file_name}"
lookup_df = (
    spark.read.format("csv")
    .option("header", "true")
    .option("inferSchema", "true")
    .load(adlspath)
)

In [0]:
# reading HVFHV data
sub_directory = "TLC_Data/*/HVFHV"
adlspath = f"abfss://{container_name}@{storage_account_name}.dfs.core.windows.net/{sub_directory}/"
hvfhv_df = (
    spark.read.format("parquet")
    .option("header", "true")
    .option("inferSchema", "true")
    .load(adlspath)
)

In [0]:
# reading yellow cab data
sub_directory = "TLC_Data/*/Yellow"
adlspath = f"abfss://{container_name}@{storage_account_name}.dfs.core.windows.net/{sub_directory}/"
yellow_df = (
    spark.read.format("parquet")
    .option("header", "true")
    .option("inferSchema", "true")
    .load(adlspath)
)

In [0]:
# reading green data

sub_directory = "TLC_Data/*/Green"
adlspath = f"abfss://{container_name}@{storage_account_name}.dfs.core.windows.net/{sub_directory}/"
green_df = (
    spark.read.format("parquet")
    .option("header", "true")
    .option("inferSchema", "true")
    .load(adlspath)
)

In [0]:
# reading FHV data
sub_directory = "TLC_Data/*/FHV"
adlspath = f"abfss://{container_name}@{storage_account_name}.dfs.core.windows.net/{sub_directory}/"
fhv_df = (
    spark.read.format("parquet")
    .option("header", "true")
    .option("inferSchema", "true")
    .load(adlspath)
)

In [0]:
# omitting FHV data due to missing columns and values
# getting count of FHV trips omitted
fhv_df.count()

Out[71]: 88637990

Data Cleaning and Transformation
--

In [0]:
# filtering for only data between 2019-2023
yellow_df = yellow_df.filter(
    (year(col("tpep_pickup_datetime")).between(2019, 2023))
    & (year(col("tpep_dropoff_datetime")).between(2019, 2023))
)


green_df = green_df.filter(
    (year(col("lpep_pickup_datetime")).between(2019, 2023))
    & (year(col("lpep_dropoff_datetime")).between(2019, 2023))
)

In [0]:
# keeping only necessary columns
hvfhv_df = hvfhv_df.select(
    "pickup_datetime",
    "dropoff_datetime",
    "PULocationID",
    "DOLocationID",
    "trip_miles",
    "trip_time",
    "tolls",
)

yellow_df = yellow_df.select(
    "tpep_pickup_datetime",
    "tpep_dropoff_datetime",
    "PULocationID",
    "DOLocationID",
    "trip_distance",
    "tolls_amount",
)

green_df = green_df.select(
    "lpep_pickup_datetime",
    "lpep_dropoff_datetime",
    "PULocationID",
    "DOLocationID",
    "trip_distance",
    "tolls_amount",
)

In [0]:
# renaming columns for consistency
yellow_df = (
    yellow_df.withColumnRenamed("tpep_pickup_datetime", "pickup_datetime")
    .withColumnRenamed("tpep_dropoff_datetime", "dropoff_datetime")
    .withColumnRenamed("trip_distance", "trip_miles")
    .withColumnRenamed("tolls_amount", "tolls")
)

green_df = (
    green_df.withColumnRenamed("lpep_pickup_datetime", "pickup_datetime")
    .withColumnRenamed("lpep_dropoff_datetime", "dropoff_datetime")
    .withColumnRenamed("trip_distance", "trip_miles")
    .withColumnRenamed("tolls_amount", "tolls")
)

In [0]:
# creating new column for trip time
time_diff = unix_timestamp(col("dropoff_datetime")) - unix_timestamp(
    col("pickup_datetime")
)
yellow_df = yellow_df.withColumn("trip_time", time_diff)
green_df = green_df.withColumn("trip_time", time_diff)

In [0]:
# converting trip time column values from seconds to hours
hvfhv_df = hvfhv_df.withColumn("trip_time", (col("trip_time") / 3600))
yellow_df = yellow_df.withColumn("trip_time", (col("trip_time") / 3600))
green_df = green_df.withColumn("trip_time", (col("trip_time") / 3600))

In [0]:
# creating a source identifier
hvfhv_df = hvfhv_df.withColumn("service", lit("HVFHV"))
yellow_df = yellow_df.withColumn("service", lit("Yellow Taxi"))
green_df = green_df.withColumn("service", lit("Green Taxi"))

In [0]:
# combining datasets
merged_df = hvfhv_df.unionAll(yellow_df).unionAll(green_df)

In [0]:
# merging lookup table to TLC data on pick up location
int_df = merged_df.alias("a").join(
    lookup_df.alias("b"),
    merged_df["PULocationID"] == lookup_df["location_i"].alias("PU_Zone"),
    how="left",
)

In [0]:
# renaming columns for clarity
int_df = int_df.withColumnRenamed("location_i", "PU_id").withColumnRenamed(
    "CBD_Zone", "PU_Zone"
)

In [0]:
# merging lookup table to TLC data on drop off location
df = int_df.join(
    lookup_df, int_df["DOLocationID"] == lookup_df["location_i"], how="left"
)

In [0]:
# renaming new columns
df = df.withColumnRenamed("CBD_Zone", "DO_Zone")

In [0]:
# dropping redundant columns
df = df.drop("PU_id", "location_i")

In [0]:
# creating new column indicating whether a trip was picked up or dropped off in CBD using filters
pu_filter = col("PU_Zone").like("CBD")
do_filter = col("DO_Zone").like("CBD")

# df = df.withColumn(
# "CBD_Check",
# when((pu_filter & do_filter), "CBD")
# .when(pu_filter | do_filter, "Partial CBD")
# .otherwise("Not CBD"))

df = df.withColumn(
    "CBD_Check", when((pu_filter | do_filter), "CBD").otherwise("Not CBD")
)

In [0]:
# extracting day of week, hour, month, and year from pick up datetime
df = (
    df.withColumn("hour", hour("pickup_datetime"))
    .withColumn("month_year", date_format("pickup_datetime", "MM-yyyy"))
    .withColumn("day_of_week", dayofweek("pickup_datetime"))
    .withColumn("year", year("pickup_datetime"))
)

In [0]:
# creating column to indicate whether the pick up date was during weekday or weekend
df = df.withColumn(
    "Weekday_Check",
    when(df["day_of_week"].isin([1, 7]), "Weekend").otherwise("Weekday"),
)

In [0]:
# dropping unnecessary columns
df = df.drop("pickup_datetime", "dropoff_datetime", "day_of_week")

In [0]:
# showing final data frame
df.display()

PULocationID DOLocationID trip_miles trip_time tolls service PU_Zone DO_Zone CBD_Check hour month_year year Weekday_Check 245 251 2.45 0.16083333333333333 0.0 HVFHV Other Other Not CBD 0 02-2019 2019 Weekday 216 197 1.71 0.1361111111111111 0.0 HVFHV Other Other Not CBD 0 02-2019 2019 Weekday 261 234 5.01 0.5997222222222223 0.0 HVFHV CBD CBD CBD 0 02-2019 2019 Weekday 87 87 0.34 0.04972222222222222 0.0 HVFHV CBD CBD CBD 0 02-2019 2019 Weekday 87 198 6.84 0.49972222222222223 0.11 HVFHV CBD Other CBD 0 02-2019 2019 Weekday 198 198 1.11 0.09972222222222223 0.0 HVFHV Other Other Not CBD 0 02-2019 2019 Weekday 161 148 4.53 0.49972222222222223 0.0 HVFHV CBD CBD CBD 0 02-2019 2019 Weekday 148 21 11.24 0.48305555555555557 0.72 HVFHV CBD Other CBD 0 02-2019 2019 Weekday 226 260 1.59 0.15944444444444444 0.0 HVFHV Queens Buffer Other Not CBD 0 02-2019 2019 Weekday 7 223 1.9 0.13166666666666665 0.0 HVFHV Queens Buffer Queens Buffer Not CBD 0 02-2019 2019 Weekday 129 70 2.74 0.16 0.0 HVFHV Other Other Not CBD 0 02-2019 2019 Weekday 263 229 7.91 0.3402777777777778 0.0 HVFHV Manhattan Buffer CBD CBD 0 02-2019 2019 Weekday 162 129 7.21 0.3188888888888889 5.76 HVFHV CBD Other CBD 0 02-2019 2019 Weekday 161 33 6.93 0.34833333333333333 0.0 HVFHV CBD Brooklyn Buffer CBD 0 02-2019 2019 Weekday 258 197 2.16 0.12166666666666667 0.0 HVFHV Other Other Not CBD 0 02-2019 2019 Weekday 255 17 2.92 0.19722222222222222 0.0 HVFHV Brooklyn Buffer Other Not CBD 0 02-2019 2019 Weekday 255 112 1.09 0.08277777777777778 0.0 HVFHV Brooklyn Buffer Brooklyn Buffer Not CBD 0 02-2019 2019 Weekday 234 137 0.37 0.05333333333333334 0.0 HVFHV CBD CBD CBD 0 02-2019 2019 Weekday 163 256 8.09 0.47888888888888886 5.76 HVFHV CBD Brooklyn Buffer CBD 0 02-2019 2019 Weekday 161 262 2.4 0.15583333333333332 0.0 HVFHV CBD Manhattan Buffer CBD 0 02-2019 2019 Weekday 4 114 1.17 0.16027777777777777 0.0 HVFHV CBD CBD CBD 0 02-2019 2019 Weekday 113 48 3.84 0.32805555555555554 0.0 HVFHV CBD CBD CBD 0 02-2019 2019 Weekday 97 17 1.36 0.11194444444444444 0.0 HVFHV Brooklyn Buffer Other Not CBD 0 02-2019 2019 Weekday 17 225 1.47 0.1338888888888889 0.0 HVFHV Other Other Not CBD 0 02-2019 2019 Weekday 225 39 5.01 0.28944444444444445 0.0 HVFHV Other Other Not CBD 0 02-2019 2019 Weekday 39 76 3.87 0.24916666666666668 0.0 HVFHV Other Other Not CBD 0 02-2019 2019 Weekday 7 7 0.65 0.10777777777777778 0.0 HVFHV Queens Buffer Queens Buffer Not CBD 0 02-2019 2019 Weekday 7 7 0.77 0.10222222222222223 0.0 HVFHV Queens Buffer Queens Buffer Not CBD 0 02-2019 2019 Weekday 249 226 5.71 0.4330555555555556 0.24 HVFHV CBD Queens Buffer CBD 0 02-2019 2019 Weekday 188 35 3.22 0.21 0.0 HVFHV Other Other Not CBD 0 02-2019 2019 Weekday 62 91 1.74 0.14583333333333334 0.0 HVFHV Other Other Not CBD 0 02-2019 2019 Weekday 71 85 1.2 0.09472222222222222 0.0 HVFHV Other Other Not CBD 0 02-2019 2019 Weekday 42 142 5.72 0.25055555555555553 0.0 HVFHV Other Manhattan Buffer Not CBD 0 02-2019 2019 Weekday 239 151 1.97 0.16916666666666666 0.0 HVFHV Manhattan Buffer Manhattan Buffer Not CBD 0 02-2019 2019 Weekday 239 151 1.5 0.0875 0.0 HVFHV Manhattan Buffer Manhattan Buffer Not CBD 0 02-2019 2019 Weekday 255 37 2.61 0.2311111111111111 0.0 HVFHV Brooklyn Buffer Other Not CBD 0 02-2019 2019 Weekday 132 39 10.42 0.3047222222222222 0.0 HVFHV Airport Other Not CBD 0 02-2019 2019 Weekday 62 61 1.02 0.08166666666666667 0.0 HVFHV Other Other Not CBD 0 02-2019 2019 Weekday 62 108 6.9 0.4025 0.0 HVFHV Other Other Not CBD 0 02-2019 2019 Weekday 88 24 8.06 0.48333333333333334 0.0 HVFHV CBD Manhattan Buffer CBD 0 02-2019 2019 Weekday 7 223 1.15 0.08305555555555555 0.0 HVFHV Queens Buffer Queens Buffer Not CBD 0 02-2019 2019 Weekday 158 137 2.79 0.26805555555555555 0.0 HVFHV CBD CBD CBD 0 02-2019 2019 Weekday 161 231 3.96 0.24972222222222223 0.0 HVFHV CBD CBD CBD 0 02-2019 2019 Weekday 138 145 7.04 0.2275 0.0 HVFHV Airport Queens Buffer Not CBD 0 02-2019 2019 Weekday 79 211 1.13 0.125 0.0 HVFHV CBD CBD CBD 0 02-2019 2019 Weekday 97 188 2.92 0.2

Summary Tables
--

In [0]:
# checking our numbers against the TLC Data Hub numbers

validation = (
    df.groupBy("service", "month_year", "CBD_Check")
    .agg(count("*"))
    .alias("Trips")
    .orderBy("month_year", "CBD_Check")
)

validation.display(5)

service month_year CBD_Check count(1) Yellow Taxi 01-2019 CBD 5487648 Green Taxi 01-2019 CBD 53155 Yellow Taxi 01-2019 Not CBD 2211508 Green Taxi 01-2019 Not CBD 625490 Yellow Taxi 01-2020 CBD 4633224 Green Taxi 01-2020 CBD 36485 HVFHV 01-2020 CBD 7665424 Yellow Taxi 01-2020 Not CBD 1776172 Green Taxi 01-2020 Not CBD 415592 HVFHV 01-2020 Not CBD 13016074 Yellow Taxi 01-2021 CBD 835129 HVFHV 01-2021 CBD 3102431 Green Taxi 01-2021 CBD 6147 Green Taxi 01-2021 Not CBD 70889 HVFHV 01-2021 Not CBD 8888010 Yellow Taxi 01-2021 Not CBD 535641 HVFHV 01-2022 CBD 5014362 Yellow Taxi 01-2022 CBD 1701532 Green Taxi 01-2022 CBD 5770 HVFHV 01-2022 Not CBD 9827004 Yellow Taxi 01-2022 Not CBD 763280 Green Taxi 01-2022 Not CBD 57096 HVFHV 01-2023 CBD 6776380 Yellow Taxi 01-2023 CBD 2191847 Green Taxi 01-2023 CBD 5744 HVFHV 01-2023 Not CBD 11806267 Yellow Taxi 01-2023 Not CBD 876083 Green Taxi 01-2023 Not CBD 62909 Yellow Taxi 02-2019 CBD 5163776 Green Taxi 02-2019 CBD 49117 HVFHV 02-2019 CBD 8123080 Yellow Taxi 02-2019 Not CBD 1888014 Green Taxi 02-2019 Not CBD 572499 HVFHV 02-2019 Not CBD 12129882 Yellow Taxi 02-2020 CBD 4633911 HVFHV 02-2020 CBD 8311740 Green Taxi 02-2020 CBD 32729 Yellow Taxi 02-2020 Not CBD 1669545 Green Taxi 02-2020 Not CBD 369788 HVFHV 02-2020 Not CBD 13523902 HVFHV 02-2021 CBD 3167738 Green Taxi 02-2021 CBD 5053 Yellow Taxi 02-2021 CBD 851617 HVFHV 02-2021 Not CBD 8522191 Green Taxi 02-2021 Not CBD 59948 Yellow Taxi 02-2021 Not CBD 521013 Yellow Taxi 02-2022 CBD 2140146 HVFHV 02-2022 CBD 5985285 Green Taxi 02-2022 CBD 6791 Yellow Taxi 02-2022 Not CBD 840168 HVFHV 02-2022 Not CBD 10120487 Green Taxi 02-2022 Not CBD 62962 Yellow Taxi 02-2023 CBD 9 Yellow Taxi 02-2023 Not CBD 1 Green Taxi 02-2023 Not CBD 1 HVFHV 03-2019 CBD 9002037 Yellow Taxi 03-2019 CBD 5847122 Green Taxi 03-2019 CBD 49135 HVFHV 03-2019 Not CBD 14980470 Green Taxi 03-2019 Not CBD 600356 Yellow Taxi 03-2019 Not CBD 2022673 Yellow Taxi 03-2020 CBD 2133226 HVFHV 03-2020 CBD 4147240 Green Taxi 03-2020 CBD 17017 Yellow Taxi 03-2020 Not CBD 876227 Green Taxi 03-2020 Not CBD 208609 HVFHV 03-2020 Not CBD 9324147 Yellow Taxi 03-2021 CBD 1239020 Green Taxi 03-2021 CBD 6538 HVFHV 03-2021 CBD 4050577 Yellow Taxi 03-2021 Not CBD 687380 Green Taxi 03-2021 Not CBD 77869 HVFHV 03-2021 Not CBD 10267118 Yellow Taxi 03-2022 CBD 2650854 HVFHV 03-2022 CBD 6931923 Green Taxi 03-2022 CBD 7916 Yellow Taxi 03-2022 Not CBD 978087 HVFHV 03-2022 Not CBD 11617676 Green Taxi 03-2022 Not CBD 71034 Yellow Taxi 04-2019 CBD 5474844 HVFHV 04-2019 CBD 8106872 Green Taxi 04-2019 CBD 44550 Yellow Taxi 04-2019 Not CBD 2004385 Green Taxi 04-2019 Not CBD 528638 HVFHV 04-2019 Not CBD 13738788 HVFHV 04-2020 CBD 660428 Yellow Taxi 04-2020 CBD 125020 Green Taxi 04-2020 CBD 2715 HVFHV 04-2020 Not CBD 3681506 Yellow Taxi 04-2020 Not CBD 113256 Green Taxi 04-2020 Not CBD 33128 Yellow Taxi 04-2021 CBD 1409210 HVFHV 04-2021 CBD 4268833 Green Taxi 04-2021 CBD 6804 Yellow Taxi 04-2021 Not CBD 763302 HVFHV 04-2021 Not CBD 9928740 Green Taxi 04-2021 Not CBD 80691 Yellow Taxi 04-2022 CBD 2627634 HVFHV 04-2022 CBD 6750889 Green Taxi 04-2022 CBD 8284 Yellow Taxi 04-2022 Not CBD 973315 HVFHV 04-2022 Not CBD 11095177 Green Taxi 04-2022 Not CBD 68307 Yellow Taxi 04-2023 Not CBD 1 Yellow Taxi 05-2019 CBD 5508180 Green Taxi 05-2019 CBD 40264 HVFHV 05-2019 CBD 8413977 Yellow Taxi 05-2019 Not CBD 2093669 Green Taxi 05-2019 Not CBD 510676 HVFHV 05-2019 Not CBD 14029389 Yellow Taxi 05-2020 CBD 185533 Green Taxi 05-2020 CBD 5451 HVFHV 05-2020 CBD 1017862 Yellow Taxi 05-2020 Not CBD 163480 Green Taxi 05-2020 Not CBD 52237 HVFHV 05-2020 Not CBD 5116637 Yellow Taxi 05-2021 CBD 1674998 HVFHV 05-2021 CBD 4758518 Green Taxi 05-2021 CBD 7342 Yellow Taxi 05-2021 Not CBD 833449 Green Taxi 05-2021 Not CBD 81388 HVFHV 05-2021 Not CBD 10049011 HVFHV 05-2022 CBD 6870369 Yellow Taxi 05-2022 CBD 2600586 Green Taxi 05-2022 CBD 8126 HVFHV 05-2022 Not CBD 11384106 Green Taxi 05-2022 Not CBD 69189 Yellow Taxi 05-2022 Not CBD 988871 HVFHV 06

In [0]:
# defining a function to agreggate column values by the retrieved business day counts within a time period


def aggregate_data(df, datetime_col, offset, agg_col, new_col_name):
    """
    This function aggregates data based on the given parameters and creates a new column with the calculated result.
      Parameters:
      -----------
          df: pd.DataFrame
             The input summary table containing the data to be aggregated.

          datetime_col: datetime
             The name of the column containing datetime values used to calculate the date range.

          offset: int
             The number of months to be used for aggregation.

          agg_col: str
             The name of the column containing values to be aggregated.

          new_col_name: str
             The name of the new column in which the aggregated result will be stored.

      Returns:
          pd.DataFrame: The input summary table with the new column containing the aggregated result.

     Example:
     --------
     df = pd.DataFrame({
         'date': pd.date_range(start='2021-01-01', periods=5, freq='M'),
         'value': [100, 200, 300, 400, 500]
     })

     aggregated_df = data_agg(
         df,
         datetime_col = 'date',
         offset = 1,
         agg_col = 'value',
         new_col_name = 'result'
     )
    """

    # Convert to datetime objects and apply the offsets
    start = pd.to_datetime(df[datetime_col]).values.astype("datetime64[M]")
    end = pd.to_datetime(df[datetime_col]).values.astype(
        "datetime64[M]"
    ) + np.timedelta64(offset, "M")

    # Calculate the number of weekdays between the start and end dates
    weekdays = np.busday_count(start, end, weekmask="Mon Tue Wed Thu Fri")

    # Calculate the aggregated values for the specified column and store it in the new column
    df[new_col_name] = np.round(df[agg_col] / weekdays.astype("float"), 0)

    return df

In [0]:
# This script processes a DataFrame of transportation data, specifically focusing on the month to month weekday average trips, trip miles, and trip time within the Central Business District (CBD). It first groups the data by various factors (e.g., weekday, month, and year), counts the trips, and sums the trip miles and time. It then filters the data to only include weekdays and trips within the CBD. Lastly, it aggregates this data for each month and outputs a DataFrame with the monthly average trip count, miles, and time. This data can be used for further analysis on traffic patterns and transportation efficiency within the CBD.

monthly = (
    df.groupBy("Weekday_Check", "service", "year", "month_year", "CBD_Check")
    .agg(
        count("*").alias("trips"),
        sum("trip_miles").alias("trip_miles"),
        sum("trip_time").alias("trip_time"),
    )
    .orderBy("year", "month_year")
)

monthly = monthly.toPandas()

monthly = monthly.query("Weekday_Check == 'Weekday' & CBD_Check == 'CBD'")

aggregate_data(monthly, "month_year", 1, "trips", "monthly_trips")
aggregate_data(monthly, "month_year", 1, "trip_miles", "monthly_miles")
aggregate_data(monthly, "month_year", 1, "trip_time", "monthly_time")

monthly.display()

/databricks/spark/python/pyspark/sql/pandas/conversion.py:486: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():
/databricks/spark/python/pyspark/sql/pandas/conversion.py:498: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():


Weekday_Check service year month_year CBD_Check trips trip_miles trip_time monthly_trips monthly_miles monthly_time Weekday Yellow Taxi 2019 01-2019 CBD 4137933 1.148976227999885E7 1339914.1700016614 179910.0 499555.0 58257.0 Weekday Green Taxi 2019 01-2019 CBD 40775 300410.1600000006 40354.44999999856 1773.0 13061.0 1755.0 Weekday Yellow Taxi 2019 02-2019 CBD 3754166 1.0723608639999028E7 1331634.6800016244 187708.0 536180.0 66582.0 Weekday HVFHV 2019 02-2019 CBD 5519820 2.7549051890002005E7 2009029.8419442778 275991.0 1377453.0 100451.0 Weekday Green Taxi 2019 02-2019 CBD 35737 271160.0800000002 39801.60999999834 1787.0 13558.0 1990.0 Weekday Yellow Taxi 2019 03-2019 CBD 4049426 1.1754362189999152E7 1484534.5800018115 192830.0 559732.0 70692.0 Weekday HVFHV 2019 03-2019 CBD 5835604 2.997086830000314E7 2193424.823888062 277886.0 1427184.0 104449.0 Weekday Green Taxi 2019 03-2019 CBD 34505 259414.14999999892 37362.34999999759 1643.0 12353.0 1779.0 Weekday HVFHV 2019 04-2019 CBD 5784715 2.9720746370001893E7 2190700.289721729 262942.0 1350943.0 99577.0 Weekday Yellow Taxi 2019 04-2019 CBD 4108110 1.2049385409999408E7 1597803.7700082082 186732.0 547699.0 72627.0 Weekday Green Taxi 2019 04-2019 CBD 33124 227821.8100000004 29318.799999998697 1506.0 10356.0 1333.0 Weekday Yellow Taxi 2019 05-2019 CBD 4176687 1.2465255539998678E7 1723964.1700101658 181595.0 541968.0 74955.0 Weekday HVFHV 2019 05-2019 CBD 6071292 3.1714303031003483E7 2433203.70444474 263969.0 1378883.0 105791.0 Weekday Green Taxi 2019 05-2019 CBD 30232 201542.04999999845 23336.409999999723 1314.0 8763.0 1015.0 Weekday Yellow Taxi 2019 06-2019 CBD 3560263 1.0521622019997448E7 1447590.6000056905 178013.0 526081.0 72380.0 Weekday HVFHV 2019 06-2019 CBD 5211431 2.68765547739967E7 2089607.7636111043 260572.0 1343828.0 104480.0 Weekday Green Taxi 2019 06-2019 CBD 25710 166081.65999999974 17993.250000000513 1286.0 8304.0 900.0 Weekday HVFHV 2019 07-2019 CBD 5661223 2.858593607800015E7 2142063.067777574 246140.0 1242867.0 93133.0 Weekday Yellow Taxi 2019 07-2019 CBD 3647105 1.0525397459998662E7 1367794.2200044899 158570.0 457626.0 59469.0 Weekday Green Taxi 2019 07-2019 CBD 26505 170084.80000000075 20501.01000000012 1152.0 7395.0 891.0 Weekday Yellow Taxi 2019 08-2019 CBD 3400623 9901651.089998936 1326494.8700037627 154574.0 450075.0 60295.0 Weekday HVFHV 2019 08-2019 CBD 5394044 2.80357176580034E7 2019750.1547221353 245184.0 1274351.0 91807.0 Weekday Green Taxi 2019 08-2019 CBD 26352 175784.48999999953 24063.909999999567 1198.0 7990.0 1094.0 Weekday Yellow Taxi 2019 09-2019 CBD 3424476 1.0211152299998555E7 1408572.0100049681 163070.0 486245.0 67075.0 Weekday HVFHV 2019 09-2019 CBD 5280230 2.806350257200353E7 2127155.4897221853 251440.0 1336357.0 101293.0 Weekday Green Taxi 2019 09-2019 CBD 25647 178238.45999999982 25626.459999999362 1221.0 8488.0 1220.0 Weekday HVFHV 2019 10-2019 CBD 6030583 3.1520888601002757E7 2385521.0836108266 262199.0 1370473.0 103718.0 Weekday Yellow Taxi 2019 10-2019 CBD 3968266 1.1632265169998799E7 1590113.5100078965 172533.0 505751.0 69135.0 Weekday Green Taxi 2019 10-2019 CBD 30108 209954.89999999997 29147.559999998794 1309.0 9128.0 1267.0 Weekday Yellow Taxi 2019 11-2019 CBD 3521245 1.0162821029999157E7 1359475.5500041808 167678.0 483944.0 64737.0 Weekday HVFHV 2019 11-2019 CBD 5440159 2.866168982099767E7 2140575.184722297 259055.0 1364842.0 101932.0 Weekday Green Taxi 2019 11-2019 CBD 26122 145683.81000000006 24517.00999999948 1244.0 6937.0 1167.0 Weekday Yellow Taxi 2019 12-2019 CBD 3570087 1.036148038000018E7 1389477.470004679 162277.0 470976.0 63158.0 Weekday HVFHV 2019 12-2019 CBD 5549029 2.8609922180997584E7 2196081.1311111497 252229.0 1300451.0 99822.0 Weekday Green Taxi 2019 12-2019 CBD 25273 239534.62999999948 24983.459999999428 1149.0 10888.0 1136.0 Weekday HVFHV 2020 01-2020 CBD 5472951 2.816222550200246E7 1897751.4722223328 237954.0 1224445.0 82511.0 Weekday Yellow Taxi 2020 01-2020 CBD 3511780 1.0048523349999087E7 1219702.5900021174 15

In [0]:
# This script processes a DataFrame of transportation data, focusing specifically on the hourly weekday average trips, trip miles, and trip time within the Central Business District (CBD). It first groups the data by various factors (e.g., weekday, hour, and whether the trip is within the CBD), counts the trips, and sums up the trip miles and time. The data is then filtered to only include weekdays and trips within the CBD. Lastly, it aggregates this data for each hour of the day and outputs a DataFrame with the hourly average trip count, miles, and time. This information can be used for a more granular analysis of traffic patterns and transportation efficiency within the CBD during different hours of the day.

hourly = (
    df.groupBy("Weekday_Check", "service", "hour", "CBD_Check")
    .agg(
        count("*").alias("trips"),
        sum("trip_miles").alias("trip_miles"),
        sum("trip_time").alias("trip_time"),
    )
    .orderBy("hour")
)

hourly = hourly.toPandas()

hourly = hourly.query("Weekday_Check == 'Weekday' & CBD_Check == 'CBD'")

aggregate_data(hourly, "hour", 1, "trips", "hourly_trips")
aggregate_data(hourly, "hour", 12, "trip_miles", "hourly_miles")
aggregate_data(hourly, "hour", 12, "trip_time", "hourly_time")

hourly.display()

/databricks/spark/python/pyspark/sql/pandas/conversion.py:486: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():
/databricks/spark/python/pyspark/sql/pandas/conversion.py:498: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():


Weekday_Check service hour CBD_Check trips trip_miles trip_time hourly_trips hourly_miles hourly_time Weekday HVFHV 0 CBD 5482531 3.253897395999999E7 1686541.8352777772 249206.0 124670.0 6462.0 Weekday Yellow Taxi 0 CBD 2041569 8199238.089999992 683272.2499999717 92799.0 31415.0 2618.0 Weekday Green Taxi 0 CBD 7197 73618.36999999997 2715.580000000001 327.0 282.0 10.0 Weekday HVFHV 1 CBD 3344596 1.964213686700001E7 971984.1094444457 152027.0 75257.0 3724.0 Weekday Yellow Taxi 1 CBD 1168900 4728181.259999999 292786.01000000304 53132.0 18116.0 1122.0 Weekday Green Taxi 1 CBD 4543 29304.52 2060.5800000000004 206.0 112.0 8.0 Weekday HVFHV 2 CBD 2168299 1.282449270500001E7 619441.5822222218 98559.0 49136.0 2373.0 Weekday Yellow Taxi 2 CBD 707555 3761165.3900000025 146162.1700000002 32162.0 14411.0 560.0 Weekday Green Taxi 2 CBD 3055 20673.52999999999 1540.3900000000006 139.0 79.0 6.0 Weekday HVFHV 3 CBD 1502456 1.009021925699999E7 450307.66527777823 68293.0 38660.0 1725.0 Weekday Yellow Taxi 3 CBD 452555 2558169.499999999 163025.61000000034 20571.0 9801.0 625.0 Weekday Green Taxi 3 CBD 3614 205177.94999999998 4480.310000000001 164.0 786.0 17.0 Weekday HVFHV 4 CBD 1715341 1.4423357691000002E7 573895.3008333329 77970.0 55262.0 2199.0 Weekday Yellow Taxi 4 CBD 427824 4463270.969999999 387934.46000000305 19447.0 17101.0 1486.0 Weekday Green Taxi 4 CBD 6589 697026.2999999999 9442.85 300.0 2671.0 36.0 Weekday HVFHV 5 CBD 2700881 2.2463800712000027E7 930872.8469444438 122767.0 86068.0 3567.0 Weekday Yellow Taxi 5 CBD 755192 1.0417284150000004E7 696935.9599999721 34327.0 39913.0 2670.0 Weekday Green Taxi 5 CBD 13347 678764.57 24372.509999999875 607.0 2601.0 93.0 Weekday HVFHV 6 CBD 5077629 3.361597365200004E7 1733472.3277777787 230801.0 128797.0 6642.0 Weekday Yellow Taxi 6 CBD 2139929 1.439263415999999E7 1147907.770000059 97270.0 55144.0 4398.0 Weekday Green Taxi 6 CBD 26895 3184492.75 54640.7299999999 1222.0 12201.0 209.0 Weekday HVFHV 7 CBD 7646378 4.154773991400008E7 2760722.168055553 347563.0 159187.0 10577.0 Weekday Yellow Taxi 7 CBD 3756242 2.0470658890000083E7 1461505.6600001603 170738.0 78432.0 5600.0 Weekday Green Taxi 7 CBD 40531 3732613.64 57645.02999999988 1842.0 14301.0 221.0 Weekday HVFHV 8 CBD 10173111 4.800592683699988E7 3874028.661666666 462414.0 183931.0 14843.0 Weekday Yellow Taxi 8 CBD 4796751 2.2956998999999985E7 1591615.2800002028 218034.0 87958.0 6098.0 Weekday Green Taxi 8 CBD 54423 3089393.119999999 59622.98999999995 2474.0 11837.0 228.0 Weekday HVFHV 9 CBD 9607505 4.538881579500006E7 3662924.438055536 436705.0 173904.0 14034.0 Weekday Yellow Taxi 9 CBD 4824747 1.6417914260000005E7 1696158.6100002348 219307.0 62904.0 6499.0 Weekday Green Taxi 9 CBD 55095 3034498.6999999993 58908.879999999896 2504.0 11626.0 226.0 Weekday HVFHV 10 CBD 7905212 4.027648017700003E7 3074530.2749999966 359328.0 154316.0 11780.0 Weekday Yellow Taxi 10 CBD 4655979 1.5509328560000006E7 1841734.590000242 211635.0 59423.0 7056.0 Weekday Green Taxi 10 CBD 47231 2545983.470000001 49832.60999999985 2147.0 9755.0 191.0 Weekday HVFHV 11 CBD 7730046 4.021117341400006E7 3051808.8438888798 351366.0 154066.0 11693.0 Weekday Yellow Taxi 11 CBD 4796936 1.6897256619999945E7 2015611.7300002216 218043.0 64740.0 7723.0 Weekday Green Taxi 11 CBD 40688 1887443.7299999997 44096.05999999984 1849.0 7232.0 169.0 Weekday HVFHV 12 CBD 7895469 4.156581590800002E7 3123292.6266666716 358885.0 159256.0 11967.0 Weekday Yellow Taxi 12 CBD 5035683 1.7089894280000027E7 2296610.780000192 228895.0 65479.0 8799.0 Weekday Green Taxi 12 CBD 35775 1573235.259999999 37611.14999999984 1626.0 6028.0 144.0 Weekday HVFHV 13 CBD 7918092 4.279328294600007E7 3212054.3244444476 359913.0 163959.0 12307.0 Weekday Yellow Taxi 13 CBD 5122991 1.8943769549999952E7 2543667.250000094 232863.0 72581.0 9746.0 Weekday Green Taxi 13 CBD 31106 1918344.5200000012 29971.31999999984 1414.0 7350.0 115.0 Weekday HVFHV 14 CBD 8226255 4.476991037099999E7 3592712.65972223 373921.0 171532.0 13765.0 Weekday Yel

In [0]:
# summing monthly average weekday number of pickups

pickup = (
    df.groupBy("service", "year", "month_year", "PULocationID")
    .agg(count("*").alias("monthly_total"))
    .orderBy("year", "month_year")
)

pickup = pickup.toPandas()

aggregate_data(pickup, "month_year", 1, "monthly_total", "daily_average")

pickup.display()

/databricks/spark/python/pyspark/sql/pandas/conversion.py:486: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():
/databricks/spark/python/pyspark/sql/pandas/conversion.py:498: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():


service year month_year PULocationID monthly_total daily_average Yellow Taxi 2019 01-2019 211 55700 2422.0 Yellow Taxi 2019 01-2019 75 57761 2511.0 Yellow Taxi 2019 01-2019 50 62841 2732.0 Yellow Taxi 2019 01-2019 79 194199 8443.0 Yellow Taxi 2019 01-2019 233 95286 4143.0 Yellow Taxi 2019 01-2019 158 69445 3019.0 Yellow Taxi 2019 01-2019 41 28913 1257.0 Yellow Taxi 2019 01-2019 144 66952 2911.0 Yellow Taxi 2019 01-2019 152 6961 303.0 Yellow Taxi 2019 01-2019 237 332796 14469.0 Yellow Taxi 2019 01-2019 88 27350 1189.0 Yellow Taxi 2019 01-2019 148 87825 3818.0 Yellow Taxi 2019 01-2019 263 156414 6801.0 Yellow Taxi 2019 01-2019 107 177267 7707.0 Yellow Taxi 2019 01-2019 166 39568 1720.0 Yellow Taxi 2019 01-2019 33 6932 301.0 Yellow Taxi 2019 01-2019 264 159817 6949.0 Yellow Taxi 2019 01-2019 100 157020 6827.0 Yellow Taxi 2019 01-2019 137 101188 4399.0 Yellow Taxi 2019 01-2019 138 184597 8026.0 Yellow Taxi 2019 01-2019 236 323313 14057.0 Yellow Taxi 2019 01-2019 223 3525 153.0 Yellow Taxi 2019 01-2019 90 132197 5748.0 Yellow Taxi 2019 01-2019 193 5364 233.0 Green Taxi 2019 01-2019 228 1515 66.0 Green Taxi 2019 01-2019 265 206 9.0 Green Taxi 2019 01-2019 27 1 0.0 Green Taxi 2019 01-2019 86 382 17.0 Green Taxi 2019 01-2019 15 211 9.0 Green Taxi 2019 01-2019 220 1774 77.0 Green Taxi 2019 01-2019 258 724 31.0 Green Taxi 2019 01-2019 245 6 0.0 Green Taxi 2019 01-2019 204 3 0.0 Green Taxi 2019 01-2019 45 1 0.0 Green Taxi 2019 01-2019 98 297 13.0 Green Taxi 2019 01-2019 160 462 20.0 Green Taxi 2019 01-2019 164 3 0.0 Green Taxi 2019 01-2019 19 423 18.0 Green Taxi 2019 01-2019 128 99 4.0 Green Taxi 2019 01-2019 58 66 3.0 Green Taxi 2019 01-2019 89 3954 172.0 Green Taxi 2019 01-2019 115 51 2.0 Green Taxi 2019 01-2019 226 5403 235.0 Green Taxi 2019 01-2019 77 1376 60.0 Green Taxi 2019 01-2019 232 1 0.0 Green Taxi 2019 01-2019 256 3436 149.0 Green Taxi 2019 01-2019 250 1339 58.0 Green Taxi 2019 01-2019 22 1390 60.0 Green Taxi 2019 01-2019 120 56 2.0 Green Taxi 2019 01-2019 198 619 27.0 Green Taxi 2019 01-2019 221 41 2.0 Green Taxi 2019 01-2019 6 16 1.0 Green Taxi 2019 01-2019 112 4135 180.0 Green Taxi 2019 01-2019 30 4 0.0 Green Taxi 2019 01-2019 129 16948 737.0 Green Taxi 2019 01-2019 208 818 36.0 Green Taxi 2019 01-2019 44 4 0.0 Green Taxi 2019 01-2019 126 757 33.0 Green Taxi 2019 01-2019 111 17 1.0 Green Taxi 2019 01-2019 170 11 0.0 Green Taxi 2019 01-2019 185 1297 56.0 Green Taxi 2019 01-2019 7 26377 1147.0 Green Taxi 2019 01-2019 181 14347 624.0 Green Taxi 2019 01-2019 244 15960 694.0 Green Taxi 2019 01-2019 72 2562 111.0 Green Taxi 2019 01-2019 93 244 11.0 Green Taxi 2019 01-2019 219 437 19.0 Green Taxi 2019 01-2019 139 597 26.0 Green Taxi 2019 01-2019 206 42 2.0 Green Taxi 2019 01-2019 225 4039 176.0 Green Taxi 2019 01-2019 24 1840 80.0 Green Taxi 2019 01-2019 229 1 0.0 Green Taxi 2019 01-2019 253 25 1.0 Green Taxi 2019 01-2019 28 1092 47.0 Green Taxi 2019 01-2019 165 2031 88.0 Green Taxi 2019 01-2019 260 12463 542.0 Green Taxi 2019 01-2019 179 4533 197.0 Green Taxi 2019 01-2019 180 320 14.0 Green Taxi 2019 01-2019 216 1492 65.0 Green Taxi 2019 01-2019 149 1243 54.0 Green Taxi 2019 01-2019 118 14 1.0 Green Taxi 2019 01-2019 202 97 4.0 Green Taxi 2019 01-2019 31 178 8.0 Green Taxi 2019 01-2019 5 4 0.0 Green Taxi 2019 01-2019 76 5683 247.0 Green Taxi 2019 01-2019 57 39 2.0 Green Taxi 2019 01-2019 71 2193 95.0 Green Taxi 2019 01-2019 172 9 0.0 Green Taxi 2019 01-2019 238 2 0.0 Green Taxi 2019 01-2019 194 27 1.0 Green Taxi 2019 01-2019 163 2 0.0 Green Taxi 2019 01-2019 81 1227 53.0 Green Taxi 2019 01-2019 26 2386 104.0 Green Taxi 2019 01-2019 201 67 3.0 Green Taxi 2019 01-2019 263 391 17.0 Green Taxi 2019 01-2019 55 2690 117.0 Green Taxi 2019 01-2019 29 1230 53.0 Green Taxi 2019 01-2019 124 473 21.0 Green Taxi 2019 01-2019 255 10428 453.0 Green Taxi 2019 01-2019 119 1258 55.0 Green Taxi 2019 01-2019 213 2661 116.0 Green Taxi 2019 01-2019 73 185 8.0 Green Taxi 2019 01-2019 146 3390 147.0 Green Taxi 2019 01-2019 96 42 2.0 Green Taxi 2019 01-

In [0]:
# summing monthly average weekday number of dropoffs

dropoff = (
    df.groupBy("service", "year", "month_year", "DOLocationID")
    .agg(count("*").alias("monthly_total"))
    .orderBy("year", "month_year")
)

dropoff = dropoff.toPandas()

aggregate_data(dropoff, "month_year", 1, "monthly_total", "daily_average")

dropoff.display()

/databricks/spark/python/pyspark/sql/pandas/conversion.py:486: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():
/databricks/spark/python/pyspark/sql/pandas/conversion.py:498: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():


service year month_year DOLocationID monthly_total daily_average Yellow Taxi 2019 01-2019 193 6335 275.0 Green Taxi 2019 01-2019 113 1033 45.0 Green Taxi 2019 01-2019 228 2789 121.0 Green Taxi 2019 01-2019 265 1102 48.0 Green Taxi 2019 01-2019 27 21 1.0 Green Taxi 2019 01-2019 86 659 29.0 Green Taxi 2019 01-2019 12 50 2.0 Green Taxi 2019 01-2019 15 329 14.0 Green Taxi 2019 01-2019 220 1634 71.0 Green Taxi 2019 01-2019 144 898 39.0 Green Taxi 2019 01-2019 258 1581 69.0 Green Taxi 2019 01-2019 45 988 43.0 Green Taxi 2019 01-2019 245 23 1.0 Green Taxi 2019 01-2019 204 11 0.0 Green Taxi 2019 01-2019 98 458 20.0 Green Taxi 2019 01-2019 160 2064 90.0 Green Taxi 2019 01-2019 164 1451 63.0 Green Taxi 2019 01-2019 19 491 21.0 Green Taxi 2019 01-2019 128 194 8.0 Green Taxi 2019 01-2019 58 73 3.0 Green Taxi 2019 01-2019 89 4666 203.0 Green Taxi 2019 01-2019 115 109 5.0 Green Taxi 2019 01-2019 226 8179 356.0 Green Taxi 2019 01-2019 232 1242 54.0 Green Taxi 2019 01-2019 77 1393 61.0 Green Taxi 2019 01-2019 256 3712 161.0 Green Taxi 2019 01-2019 22 1228 53.0 Green Taxi 2019 01-2019 120 136 6.0 Green Taxi 2019 01-2019 250 1263 55.0 Green Taxi 2019 01-2019 198 1615 70.0 Green Taxi 2019 01-2019 221 80 3.0 Green Taxi 2019 01-2019 6 35 2.0 Green Taxi 2019 01-2019 112 5212 227.0 Green Taxi 2019 01-2019 30 24 1.0 Green Taxi 2019 01-2019 129 16118 701.0 Green Taxi 2019 01-2019 208 1112 48.0 Green Taxi 2019 01-2019 44 20 1.0 Green Taxi 2019 01-2019 126 943 41.0 Green Taxi 2019 01-2019 170 2666 116.0 Green Taxi 2019 01-2019 111 61 3.0 Green Taxi 2019 01-2019 185 1331 58.0 Green Taxi 2019 01-2019 7 16781 730.0 Green Taxi 2019 01-2019 181 11986 521.0 Green Taxi 2019 01-2019 244 9079 395.0 Green Taxi 2019 01-2019 219 734 32.0 Green Taxi 2019 01-2019 72 2511 109.0 Green Taxi 2019 01-2019 139 718 31.0 Green Taxi 2019 01-2019 93 579 25.0 Green Taxi 2019 01-2019 206 79 3.0 Green Taxi 2019 01-2019 225 5544 241.0 Green Taxi 2019 01-2019 24 3023 131.0 Green Taxi 2019 01-2019 229 1905 83.0 Green Taxi 2019 01-2019 253 54 2.0 Green Taxi 2019 01-2019 28 2857 124.0 Green Taxi 2019 01-2019 165 1778 77.0 Green Taxi 2019 01-2019 260 7354 320.0 Green Taxi 2019 01-2019 179 6393 278.0 Green Taxi 2019 01-2019 180 414 18.0 Green Taxi 2019 01-2019 216 3264 142.0 Green Taxi 2019 01-2019 149 1183 51.0 Green Taxi 2019 01-2019 118 32 1.0 Green Taxi 2019 01-2019 202 364 16.0 Green Taxi 2019 01-2019 31 226 10.0 Green Taxi 2019 01-2019 5 27 1.0 Green Taxi 2019 01-2019 76 5460 237.0 Green Taxi 2019 01-2019 57 275 12.0 Green Taxi 2019 01-2019 2 6 0.0 Green Taxi 2019 01-2019 238 9439 410.0 Green Taxi 2019 01-2019 71 2229 97.0 Green Taxi 2019 01-2019 172 24 1.0 Green Taxi 2019 01-2019 163 1822 79.0 Green Taxi 2019 01-2019 194 199 9.0 Green Taxi 2019 01-2019 201 181 8.0 Green Taxi 2019 01-2019 81 1192 52.0 Green Taxi 2019 01-2019 26 2400 104.0 Green Taxi 2019 01-2019 68 1911 83.0 Green Taxi 2019 01-2019 263 7212 314.0 Green Taxi 2019 01-2019 55 2071 90.0 Green Taxi 2019 01-2019 211 571 25.0 Green Taxi 2019 01-2019 29 1029 45.0 Green Taxi 2019 01-2019 124 600 26.0 Green Taxi 2019 01-2019 255 3413 148.0 Green Taxi 2019 01-2019 213 2609 113.0 Green Taxi 2019 01-2019 119 1708 74.0 Green Taxi 2019 01-2019 73 506 22.0 Green Taxi 2019 01-2019 146 2940 128.0 Green Taxi 2019 01-2019 96 247 11.0 Green Taxi 2019 01-2019 60 851 37.0 Green Taxi 2019 01-2019 16 655 28.0 Green Taxi 2019 01-2019 65 5281 230.0 Green Taxi 2019 01-2019 239 5716 249.0 Green Taxi 2019 01-2019 67 743 32.0 Green Taxi 2019 01-2019 236 10586 460.0 Green Taxi 2019 01-2019 222 1353 59.0 Green Taxi 2019 01-2019 56 9816 427.0 Green Taxi 2019 01-2019 109 31 1.0 Green Taxi 2019 01-2019 21 1089 47.0 Green Taxi 2019 01-2019 183 476 21.0 Green Taxi 2019 01-2019 261 816 35.0 Green Taxi 2019 01-2019 117 1073 47.0 Green Taxi 2019 01-2019 176 9 0.0 Green Taxi 2019 01-2019 106 2155 94.0 Green Taxi 2019 01-2019 11 558 24.0 Green Taxi 2019 01-2019 66 3163 138.0 Green Taxi 2019 01-2019 161 2743 119.0 Green Taxi 2019 01-2019 40 4411 192.0 Green